# Poisson's equation on the Torus

Poisson's equation is given as

$$
\nabla^2 u = f.
$$

In this notebook we will solve this equation (without boundary conditions) on the surface of a torus, using curvilinear coordinates. The surface of the torus is parametrized by    

$$
\begin{align}
x(\theta, \phi) &= (R + r \cos \theta) \cos \phi \\
y(\theta, \phi) &= (R + r \cos \theta) \sin \phi \\
z(\theta, \phi) &= r \sin \theta
\end{align}
$$
where $\theta, \phi$ are angles which make a full circle, so that their values start and end at the same point, $R$ is the distance from the center of the tube to the center of the torus,
$r$ is the radius of the tube. Note that $\theta$ is the angle in the small circle (around its center), whereas $\phi$ is the angle of the large circle, around origo.

We start the implementation by importing necessary functionality from shenfun and sympy and then defining the coordinates of the surface of the torus. Note that `rv` represents the position vector spanning the surface.

In [1]:
from shenfun import *
from shenfun.la import Solver2D
import sympy as sp
from IPython.display import Math

N = 20
R = 3
r = 1
theta, phi = psi = sp.symbols('x,y', real=True, positive=True)
rv = ((R + r*sp.cos(theta))*sp.cos(phi), (R + r*sp.cos(theta))*sp.sin(phi), r*sp.sin(theta)) 

Now create necessary bases and function spaces. Due to the geometry of the problem, the solution will be periodic in both $\theta$ and $\phi$ directions, and we choose Fourier basis functions. The basis for the $\phi$-direction can be either real to complex or complex to complex, depending on the type of the solution. Here we assume a real solution

In [2]:
B1 = Basis(N, 'F', dtype='D', domain=(0, 2*np.pi))
B2 = Basis(N, 'F', dtype='d', domain=(0, 2*np.pi))
T = TensorProductSpace(comm, (B1, B2), coordinates=(psi, rv, sp.Q.positive(r*sp.cos(theta)+R)))
V = VectorTensorProductSpace(T)
u = TrialFunction(T)
v = TestFunction(T)

Note the assumption `sp.Q.positive(r*sp.cos(theta)+R))`, which is there to help sympy when computing basis vectors and scaling factors. It is not completely necessary, but try to omit it and look at what happens to the expanded Poisson equation below.

In [3]:
alpha = 1
du = div(grad(u))+alpha*u
Math(du.tolatex(symbol_names={r: 'r', theta: '\\theta', phi: '\\phi'}))

<IPython.core.display.Math object>

We now create a manufactured solution that satisfies periodicity and compute the right hand side $f$.

In [4]:
ue = sp.sin(theta*2)*sp.cos(4*phi)
f = (div(grad(u))+alpha*u).tosympy(basis=ue, psi=psi)
fj = Array(T, buffer=f)
f_hat = Function(T)
f_hat = inner(v, fj, output_array=f_hat)

Assemble coefficient matrix and solve problem

In [5]:
mats = inner(v, (div(grad(u))+alpha*u), level=2)
u_hat = Function(T)
sol = Solver2D(mats)
u_hat = sol(f_hat, u_hat)
uj = u_hat.backward()
uq = Array(T, buffer=ue)
print('Error =', np.linalg.norm(uj-uq))

Error = 3.0414336387426026e-14


Finally, just plot the solution using mayavi. Wrap the periodic directions around and refine to get a nicer plot.

In [6]:
from mayavi import mlab
u_hat2 = u_hat.refine([N*8, N*8])
ur = u_hat2.backward(uniform=True)
xx, yy, zz = u_hat2.function_space().local_curvilinear_mesh(uniform=True)
xx = np.hstack([xx, xx[:, 0][:, None]])
yy = np.hstack([yy, yy[:, 0][:, None]])
zz = np.hstack([zz, zz[:, 0][:, None]])
ur = np.hstack([ur, ur[:, 0][:, None]])
xx = np.vstack([xx, xx[0]])
yy = np.vstack([yy, yy[0]])
zz = np.vstack([zz, zz[0]])
ur = np.vstack([ur, ur[0]])
mlab.init_notebook('x3d', 400, 400)
mlab.figure(bgcolor=(1, 1, 1))
m = mlab.mesh(xx, yy, zz, scalars=ur.real, colormap='jet')
mlab.savefig('torus.tiff')
m

Notebook initialized with x3d backend.


# Check coordinates

Here we simply check that

$$
\nabla^2 \vec{u} = \nabla \nabla \cdot \vec{u} - \nabla \times \nabla \times \vec{u}
$$
for the 3D coordinates, including the radius of the smaller circle:

In [7]:
r, theta, phi = psi = sp.symbols('x,y,z', real=True, positive=True)
rv = ((R + r*sp.cos(theta))*sp.cos(phi), (R + r*sp.cos(theta))*sp.sin(phi), r*sp.sin(theta)) 
N = 6
B0 = Basis(N, 'L', bc=(0, 0), domain=(0, 1))
B1 = Basis(N, 'F', dtype='D', domain=(0, 2*np.pi))
B2 = Basis(N, 'F', dtype='d', domain=(0, 2*np.pi))
T = TensorProductSpace(comm, (B0, B1, B2), coordinates=(psi, rv, sp.Q.positive(r*sp.cos(theta)+R)))
V = VectorTensorProductSpace(T)
p = TrialFunction(V)
du = div(grad(p))
dv = grad(div(p)) - curl(curl(p))
dw = du-dv
dw.simplify()
Math(dw.tolatex(symbol_names={r: 'r', theta: '\\theta', phi: '\\phi'}))

<IPython.core.display.Math object>

In [8]:
u = TrialFunction(T)
v = TestFunction(T)
du = div(grad(u))
Math((du).tolatex(symbol_names={r: 'r', theta: '\\theta', phi: '\\phi'}))

<IPython.core.display.Math object>

In [9]:
M = inner(v, div(grad(u))*T.hi.prod())